# 環境設定 安裝

```
$ conda install pytorch -c pytorch
$ pip install -r requirements.txt
```

In [1]:
import numpy as np
from __future__ import print_function
import argparse
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
from torchvision import datasets, transforms

torch.backends.cudnn.enabled=False

# 模型參數

In [2]:
class argements:
    batch_size = 100
    test_batch_size = 1000
    epochs = 10
    lr = 0.01
    momentum = 0.5
    no_cuda = True
    seed = 1
    log_interval = 10
    digital = 3
    
args = argements()

In [3]:
use_cuda = not args.no_cuda and torch.cuda.is_available()
use_cuda

False

In [4]:
torch.manual_seed(args.seed)

device = torch.device("cuda" if use_cuda else "cpu")
kwargs = {'num_workers': 1, 'pin_memory': True} if use_cuda else {}

# 產生 train and test Data

把所有可能的減法式子都找出來<br>
並把 80% 資料當成訓練資料 20% 當成測試資料

並且存成 `corpus/data.csv`，方便下次讀入資料

### 資料向量化

參考範例將算式與答案進行 one-hot 編碼變成向量<br>
準備餵進去 model 中

同時轉型成 `torch.Tensor` 

In [5]:
import random
import math
import os
import pandas as pd
import numpy as np

def genSubExpr(force=False):
    datadir = './corpus'
    if not os.path.isdir(datadir):
        os.mkdir(datadir)
    
    filename = datadir + '/datas.csv'
    if not force and os.path.exists(filename):
        return np.array(pd.read_csv(filename, dtype=str, header=None)).tolist()
    
    maxNum = math.pow(10,args.digital) - 1
    minNum = 0

    datas = []
    numFormat = '{:0>' + str(args.digital) + 'd}'
    for a in range(int(maxNum)):
        for b in range(a+1):
            answer = a - b
            expr = numFormat.format(a) + '-' + numFormat.format(b)
            datas.append([expr, numFormat.format(answer)])
    
    # save list to csv
    pd.DataFrame(datas).to_csv(filename, index=False, header=False)
    
    return datas

subDataSet = genSubExpr()
len(subDataSet)

499500

In [6]:
train_ratio = 0.8
test_ratio = 0.2

random.shuffle(subDataSet)

lenght = len(subDataSet)
tmp = int(lenght * train_ratio)
train_data = subDataSet[:tmp]
test_data = subDataSet[tmp:]

print(lenght, len(train_data), len(test_data))

499500 399600 99900


In [7]:
class CharacterTable(object):
    def __init__(self, chars):
        self.chars = sorted(set(chars))
        self.char_indices = dict((c, i) for i, c in enumerate(self.chars))
        self.indices_char = dict((i, c) for i, c in enumerate(self.chars))
    
    def encode(self, C, num_rows):
        x = np.zeros((num_rows, len(self.chars)))
        for i, c in enumerate(C):
            x[i, self.char_indices[c]] = 1
        return x
    
    def decode(self, x, calc_argmax=True):
        if calc_argmax:
            x = x.argmax(axis=-1)
        return "".join(self.indices_char[i] for i in x)
    
    def encodeTarget(self, C, num_rows):
        x = np.zeros((num_rows))
        for i, c in enumerate(C):
            x[i] = self.char_indices[c]
        return x

cTable = CharacterTable('0123456789-')

In [8]:
print(cTable.char_indices)
print(cTable.indices_char)
cTable.encodeTarget('023',3)

{'-': 0, '0': 1, '1': 2, '2': 3, '3': 4, '4': 5, '5': 6, '6': 7, '7': 8, '8': 9, '9': 10}
{0: '-', 1: '0', 2: '1', 3: '2', 4: '3', 5: '4', 6: '5', 7: '6', 8: '7', 9: '8', 10: '9'}


array([1., 3., 4.])

In [34]:
train_datas = []
for i in range(0, len(train_data), args.batch_size):
    tmpx = []
    tmpy = []
    for data, target in train_data[i:i+args.batch_size]:
        tmpx.append(cTable.encode(data,args.digital*2+1))
        tmpy.append(cTable.encodeTarget(target,args.digital))
    tmpx = torch.Tensor(tmpx)
    tmpy = torch.LongTensor(tmpy)
    train_datas.append([tmpx, tmpy])

test_datas = []
for i in range(0, len(test_data), args.batch_size):
    tmpx = []
    tmpy = []
    for data, target in test_data[i:i+args.batch_size]:
        tmpx.append(cTable.encode(data,args.digital*2+1))
        tmpy.append(cTable.encodeTarget(target,args.digital))
    tmpx = torch.Tensor(tmpx)
    tmpy = torch.LongTensor(tmpy)
    test_datas.append([tmpx, tmpy])

#random.shuffle(test_datas)
#test_datas = test_datas[:100]

In [35]:
print(len(train_datas),len(test_datas))
print(train_datas[0][0].shape, test_datas[0][0].shape)

3996 999
torch.Size([100, 7, 11]) torch.Size([100, 7, 11])


# 設計模型

### 設計圖

![](https://imgur.com/VchMSMG.png)

### 設計

input size 是 one-hot 編碼的字元數<br>
也就是圖中的 `7` 是 one-hot 編碼後的 input

LSTM 的 output size 是隱藏起來的 hidden_size，預設為 `128`

假設算式 `723-084` ，我會把一個文字位置當成時間序列上的一次輸入<br>
然後算式都輸入進去後，會多輸入都是 0 的向量總共是答案的位數，在這一次作業是 `3`<br>
因此我預計抓從後面數過來的三個輸出是我的答案

並放到 fully-connect 將之從 hidden size 對應到 output size (也是跟 input size 一樣的)<br>
只不過會變成 `(3, batch size, one-hot char size)` 的形式

### 設計想法

想說 LSTM 是類似於人類死背那樣把前面的輸入記憶下來<br>
就想要讓 LSTM 把輸入的算式數值記錄下來並且在之後多出來的地方把答案算出來

像是我自己看到 `723-084` 的 `7` 會先記得一個數字<br>
看到 `3` 時，腦袋數字已經是 `七百二十三` 而不是 `七`<br>
繼續看到 `-` 知道後面要把前面記起來的數字減掉<br>
看到 `0` 知道答案可能有一個 `7`，但是看到 `8` 就知道這裡會是 `-6`，再來是 `4-3=1`<br>
但答案可不能是 `7,-6,1`<br>

因此想說多幾個 input 讓 LSTM 可以記錄剛剛的結果並計算正確結果

In [27]:
class SubModel(nn.Module):
    def __init__(self, class_num, hidden_size=128):
        super(SubModel, self).__init__()
        self.class_num = class_num
        self.hidden_size = hidden_size
        self.rnn1 = nn.LSTM(class_num, hidden_size, 2)
        #self.rnn2 = nn.LSTM(110, 55, 2)
        self.fc1 = nn.Linear(hidden_size, class_num)
        #self.hidden_state = (torch.autograd.Variable(torch.zeros(2,args.batch_size,110)), torch.autograd.Variable(torch.zeros(2,args.batch_size,110)))
    
    def forward(self, x):
        x = x.transpose(0, 1)
        # x.size (seq, batch, len(chars))
        tmp = torch.autograd.Variable(torch.zeros(args.digital,args.batch_size,self.class_num))
        x = torch.cat((x, tmp), 0)
        hidden_state = (torch.autograd.Variable(torch.zeros(2,args.batch_size,self.hidden_size)), torch.autograd.Variable(torch.zeros(2,args.batch_size,self.hidden_size)))
        x, _ = self.rnn1(x, hidden_state)
        #x = F.relu(self.fc1(x))
        x = self.fc1(x)
        x = x[-args.digital:]
        x = F.softmax(x, dim=2)
        x = x.transpose(0, 1)
        # x.size (batch, seq, len(chars))
        return x

model = SubModel(len(cTable.chars)).to(device)
optimizer = optim.Adam(model.parameters(), lr=args.lr)

In [36]:
print('======== Model Layer ========\n')
for layers in model.children():
    print(layers)
print('\n=============================\n')

======== Model Layer ========

LSTM(11, 128, num_layers=2)
Linear(in_features=128, out_features=11, bias=True)




# 訓練與驗證

參考範例修改

最後經過 10 幾次訓練，驗證的準確率可以來到 `87%`

不能說是非常好的成績，但這是我目前的成果

In [19]:
class colors:
    ok = '\033[92m'
    fail = '\033[91m'
    close = '\033[0m'

def train(epoch):
    model.train()
    for batch_idx, (data, target) in enumerate(train_datas):
        data, target = torch.autograd.Variable(data), torch.autograd.Variable(target)
        data, target = data.to(device), target.to(device)
        output = model(data)
        output = output.transpose(1,2)
        # output.size (batch, len(chars), seq)
        loss = F.cross_entropy(output, target)
        loss.backward()
        optimizer.step()
        optimizer.zero_grad()
        if batch_idx % args.log_interval == 0:
            print('Train Epoch : {} [{}/{} ({:.0f}%)]\tLoss: {:.6f}'.format(
                epoch, batch_idx*len(data), len(train_datas)*len(data), 100.*batch_idx/len(train_datas), loss.item() ))
            
def test():
    model.eval()
    test_loss = 0
    test_correct = 0
    with torch.no_grad():
        for data, target in test_datas:
            data, target = torch.autograd.Variable(data), torch.autograd.Variable(target)
            data, target = data.to(device), target.to(device)
            output = model(data)
            output = output.transpose(1,2)
            # output.size (batch, len(chars), seq)
            test_loss += F.cross_entropy(output, target, size_average=False).item()
            output = output.transpose(1,2)
            # output.size (batch, seq, len(chars))
            for idx in range(args.batch_size):
                q = cTable.decode(data[idx].numpy())
                correct = cTable.decode(target[idx].numpy(), calc_argmax=False)
                guess = cTable.decode(output[idx].numpy())
                print('Q', q, end=' ')
                print('T', correct, end=' ')
                if correct == guess:
                    test_correct += 1
                    print(colors.ok + '☑' + colors.close, end=' ')
                else:
                    print(colors.fail + '☒' + colors.close, end=' ')
                print(guess)

    test_loss /= len(test_datas)*args.batch_size
    print('\nTest set: Average loss: {:.4f}, Accuracy: {}/{} ({:.0f}%)\n'.format(
        test_loss, test_correct, len(test_datas)*args.batch_size,
        100. * test_correct / (len(test_datas)*args.batch_size) ))

In [32]:
for i in range(args.epochs):
    train(i)

Train Epoch : 0 [0/399600 (0%)]	Loss: 1.583170
Train Epoch : 0 [1000/399600 (0%)]	Loss: 1.582974
Train Epoch : 0 [2000/399600 (1%)]	Loss: 1.606729
Train Epoch : 0 [3000/399600 (1%)]	Loss: 1.593707
Train Epoch : 0 [4000/399600 (1%)]	Loss: 1.573884
Train Epoch : 0 [5000/399600 (1%)]	Loss: 1.609949
Train Epoch : 0 [6000/399600 (2%)]	Loss: 1.590524
Train Epoch : 0 [7000/399600 (2%)]	Loss: 1.581761
Train Epoch : 0 [8000/399600 (2%)]	Loss: 1.566667
Train Epoch : 0 [9000/399600 (2%)]	Loss: 1.573288
Train Epoch : 0 [10000/399600 (3%)]	Loss: 1.593709
Train Epoch : 0 [11000/399600 (3%)]	Loss: 1.594082
Train Epoch : 0 [12000/399600 (3%)]	Loss: 1.582101
Train Epoch : 0 [13000/399600 (3%)]	Loss: 1.588023
Train Epoch : 0 [14000/399600 (4%)]	Loss: 1.573801
Train Epoch : 0 [15000/399600 (4%)]	Loss: 1.580365
Train Epoch : 0 [16000/399600 (4%)]	Loss: 1.603297
Train Epoch : 0 [17000/399600 (4%)]	Loss: 1.576746
Train Epoch : 0 [18000/399600 (5%)]	Loss: 1.580025
Train Epoch : 0 [19000/399600 (5%)]	Loss: 1.

Train Epoch : 0 [158000/399600 (40%)]	Loss: 1.602655
Train Epoch : 0 [159000/399600 (40%)]	Loss: 1.585356
Train Epoch : 0 [160000/399600 (40%)]	Loss: 1.568143
Train Epoch : 0 [161000/399600 (40%)]	Loss: 1.553169
Train Epoch : 0 [162000/399600 (41%)]	Loss: 1.597611
Train Epoch : 0 [163000/399600 (41%)]	Loss: 1.574461
Train Epoch : 0 [164000/399600 (41%)]	Loss: 1.587162
Train Epoch : 0 [165000/399600 (41%)]	Loss: 1.569735
Train Epoch : 0 [166000/399600 (42%)]	Loss: 1.563092
Train Epoch : 0 [167000/399600 (42%)]	Loss: 1.562423
Train Epoch : 0 [168000/399600 (42%)]	Loss: 1.607770
Train Epoch : 0 [169000/399600 (42%)]	Loss: 1.577084
Train Epoch : 0 [170000/399600 (43%)]	Loss: 1.574731
Train Epoch : 0 [171000/399600 (43%)]	Loss: 1.587638
Train Epoch : 0 [172000/399600 (43%)]	Loss: 1.581398
Train Epoch : 0 [173000/399600 (43%)]	Loss: 1.593254
Train Epoch : 0 [174000/399600 (44%)]	Loss: 1.612482
Train Epoch : 0 [175000/399600 (44%)]	Loss: 1.568362
Train Epoch : 0 [176000/399600 (44%)]	Loss: 1.

Train Epoch : 0 [313000/399600 (78%)]	Loss: 1.583277
Train Epoch : 0 [314000/399600 (79%)]	Loss: 1.583842
Train Epoch : 0 [315000/399600 (79%)]	Loss: 1.580689
Train Epoch : 0 [316000/399600 (79%)]	Loss: 1.566619
Train Epoch : 0 [317000/399600 (79%)]	Loss: 1.569871
Train Epoch : 0 [318000/399600 (80%)]	Loss: 1.599956
Train Epoch : 0 [319000/399600 (80%)]	Loss: 1.609773
Train Epoch : 0 [320000/399600 (80%)]	Loss: 1.563045
Train Epoch : 0 [321000/399600 (80%)]	Loss: 1.587470
Train Epoch : 0 [322000/399600 (81%)]	Loss: 1.563042
Train Epoch : 0 [323000/399600 (81%)]	Loss: 1.557289
Train Epoch : 0 [324000/399600 (81%)]	Loss: 1.593259
Train Epoch : 0 [325000/399600 (81%)]	Loss: 1.579802
Train Epoch : 0 [326000/399600 (82%)]	Loss: 1.587959
Train Epoch : 0 [327000/399600 (82%)]	Loss: 1.600813
Train Epoch : 0 [328000/399600 (82%)]	Loss: 1.560972
Train Epoch : 0 [329000/399600 (82%)]	Loss: 1.561606
Train Epoch : 0 [330000/399600 (83%)]	Loss: 1.584371
Train Epoch : 0 [331000/399600 (83%)]	Loss: 1.

Train Epoch : 1 [70000/399600 (18%)]	Loss: 1.580749
Train Epoch : 1 [71000/399600 (18%)]	Loss: 1.599104
Train Epoch : 1 [72000/399600 (18%)]	Loss: 1.582396
Train Epoch : 1 [73000/399600 (18%)]	Loss: 1.593128
Train Epoch : 1 [74000/399600 (19%)]	Loss: 1.578090
Train Epoch : 1 [75000/399600 (19%)]	Loss: 1.600059
Train Epoch : 1 [76000/399600 (19%)]	Loss: 1.568421
Train Epoch : 1 [77000/399600 (19%)]	Loss: 1.586563
Train Epoch : 1 [78000/399600 (20%)]	Loss: 1.569344
Train Epoch : 1 [79000/399600 (20%)]	Loss: 1.580398
Train Epoch : 1 [80000/399600 (20%)]	Loss: 1.567362
Train Epoch : 1 [81000/399600 (20%)]	Loss: 1.580307
Train Epoch : 1 [82000/399600 (21%)]	Loss: 1.573147
Train Epoch : 1 [83000/399600 (21%)]	Loss: 1.579618
Train Epoch : 1 [84000/399600 (21%)]	Loss: 1.569892
Train Epoch : 1 [85000/399600 (21%)]	Loss: 1.576910
Train Epoch : 1 [86000/399600 (22%)]	Loss: 1.559692
Train Epoch : 1 [87000/399600 (22%)]	Loss: 1.566630
Train Epoch : 1 [88000/399600 (22%)]	Loss: 1.584795
Train Epoch 

Train Epoch : 1 [226000/399600 (57%)]	Loss: 1.564037
Train Epoch : 1 [227000/399600 (57%)]	Loss: 1.589502
Train Epoch : 1 [228000/399600 (57%)]	Loss: 1.560568
Train Epoch : 1 [229000/399600 (57%)]	Loss: 1.576434
Train Epoch : 1 [230000/399600 (58%)]	Loss: 1.596432
Train Epoch : 1 [231000/399600 (58%)]	Loss: 1.587412
Train Epoch : 1 [232000/399600 (58%)]	Loss: 1.603408
Train Epoch : 1 [233000/399600 (58%)]	Loss: 1.590865
Train Epoch : 1 [234000/399600 (59%)]	Loss: 1.606042
Train Epoch : 1 [235000/399600 (59%)]	Loss: 1.586436
Train Epoch : 1 [236000/399600 (59%)]	Loss: 1.580845
Train Epoch : 1 [237000/399600 (59%)]	Loss: 1.586966
Train Epoch : 1 [238000/399600 (60%)]	Loss: 1.594597
Train Epoch : 1 [239000/399600 (60%)]	Loss: 1.590028
Train Epoch : 1 [240000/399600 (60%)]	Loss: 1.582329
Train Epoch : 1 [241000/399600 (60%)]	Loss: 1.586449
Train Epoch : 1 [242000/399600 (61%)]	Loss: 1.600072
Train Epoch : 1 [243000/399600 (61%)]	Loss: 1.582597
Train Epoch : 1 [244000/399600 (61%)]	Loss: 1.

...

Train Epoch : 3 [51000/399600 (13%)]	Loss: 1.583100
Train Epoch : 3 [52000/399600 (13%)]	Loss: 1.593068
Train Epoch : 3 [53000/399600 (13%)]	Loss: 1.569765
Train Epoch : 3 [54000/399600 (14%)]	Loss: 1.573168
Train Epoch : 3 [55000/399600 (14%)]	Loss: 1.573114
Train Epoch : 3 [56000/399600 (14%)]	Loss: 1.563088
Train Epoch : 3 [57000/399600 (14%)]	Loss: 1.602490
Train Epoch : 3 [58000/399600 (15%)]	Loss: 1.576698
Train Epoch : 3 [59000/399600 (15%)]	Loss: 1.574107
Train Epoch : 3 [60000/399600 (15%)]	Loss: 1.559772
Train Epoch : 3 [61000/399600 (15%)]	Loss: 1.576175
Train Epoch : 3 [62000/399600 (16%)]	Loss: 1.569876
Train Epoch : 3 [63000/399600 (16%)]	Loss: 1.566792
Train Epoch : 3 [64000/399600 (16%)]	Loss: 1.582585
Train Epoch : 3 [65000/399600 (16%)]	Loss: 1.589412
Train Epoch : 3 [66000/399600 (17%)]	Loss: 1.566471
Train Epoch : 3 [67000/399600 (17%)]	Loss: 1.603158
Train Epoch : 3 [68000/399600 (17%)]	Loss: 1.588627
Train Epoch : 3 [69000/399600 (17%)]	Loss: 1.576504
Train Epoch 

Train Epoch : 3 [207000/399600 (52%)]	Loss: 1.586888
Train Epoch : 3 [208000/399600 (52%)]	Loss: 1.563168
Train Epoch : 3 [209000/399600 (52%)]	Loss: 1.569387
Train Epoch : 3 [210000/399600 (53%)]	Loss: 1.593062
Train Epoch : 3 [211000/399600 (53%)]	Loss: 1.583168
Train Epoch : 3 [212000/399600 (53%)]	Loss: 1.579605
Train Epoch : 3 [213000/399600 (53%)]	Loss: 1.567396
Train Epoch : 3 [214000/399600 (54%)]	Loss: 1.583073
Train Epoch : 3 [215000/399600 (54%)]	Loss: 1.583110
Train Epoch : 3 [216000/399600 (54%)]	Loss: 1.573075
Train Epoch : 3 [217000/399600 (54%)]	Loss: 1.579758
Train Epoch : 3 [218000/399600 (55%)]	Loss: 1.589779
Train Epoch : 3 [219000/399600 (55%)]	Loss: 1.566426
Train Epoch : 3 [220000/399600 (55%)]	Loss: 1.576581
Train Epoch : 3 [221000/399600 (55%)]	Loss: 1.578711
Train Epoch : 3 [222000/399600 (56%)]	Loss: 1.575040
Train Epoch : 3 [223000/399600 (56%)]	Loss: 1.563055
Train Epoch : 3 [224000/399600 (56%)]	Loss: 1.599944
Train Epoch : 3 [225000/399600 (56%)]	Loss: 1.

Train Epoch : 3 [362000/399600 (91%)]	Loss: 1.570178
Train Epoch : 3 [363000/399600 (91%)]	Loss: 1.582557
Train Epoch : 3 [364000/399600 (91%)]	Loss: 1.583408
Train Epoch : 3 [365000/399600 (91%)]	Loss: 1.584871
Train Epoch : 3 [366000/399600 (92%)]	Loss: 1.592425
Train Epoch : 3 [367000/399600 (92%)]	Loss: 1.586696
Train Epoch : 3 [368000/399600 (92%)]	Loss: 1.572638
Train Epoch : 3 [369000/399600 (92%)]	Loss: 1.596349
Train Epoch : 3 [370000/399600 (93%)]	Loss: 1.596120
Train Epoch : 3 [371000/399600 (93%)]	Loss: 1.583955
Train Epoch : 3 [372000/399600 (93%)]	Loss: 1.561029
Train Epoch : 3 [373000/399600 (93%)]	Loss: 1.574836
Train Epoch : 3 [374000/399600 (94%)]	Loss: 1.613141
Train Epoch : 3 [375000/399600 (94%)]	Loss: 1.572407
Train Epoch : 3 [376000/399600 (94%)]	Loss: 1.574588
Train Epoch : 3 [377000/399600 (94%)]	Loss: 1.607985
Train Epoch : 3 [378000/399600 (95%)]	Loss: 1.570083
Train Epoch : 3 [379000/399600 (95%)]	Loss: 1.600489
Train Epoch : 3 [380000/399600 (95%)]	Loss: 1.

Train Epoch : 4 [120000/399600 (30%)]	Loss: 1.586426
Train Epoch : 4 [121000/399600 (30%)]	Loss: 1.586616
Train Epoch : 4 [122000/399600 (31%)]	Loss: 1.569721
Train Epoch : 4 [123000/399600 (31%)]	Loss: 1.576422
Train Epoch : 4 [124000/399600 (31%)]	Loss: 1.559776
Train Epoch : 4 [125000/399600 (31%)]	Loss: 1.547185
Train Epoch : 4 [126000/399600 (32%)]	Loss: 1.573056
Train Epoch : 4 [127000/399600 (32%)]	Loss: 1.563647
Train Epoch : 4 [128000/399600 (32%)]	Loss: 1.581189
Train Epoch : 4 [129000/399600 (32%)]	Loss: 1.566293
Train Epoch : 4 [130000/399600 (33%)]	Loss: 1.569724
Train Epoch : 4 [131000/399600 (33%)]	Loss: 1.559743
Train Epoch : 4 [132000/399600 (33%)]	Loss: 1.569811
Train Epoch : 4 [133000/399600 (33%)]	Loss: 1.593191
Train Epoch : 4 [134000/399600 (34%)]	Loss: 1.586298
Train Epoch : 4 [135000/399600 (34%)]	Loss: 1.566609
Train Epoch : 4 [136000/399600 (34%)]	Loss: 1.569794
Train Epoch : 4 [137000/399600 (34%)]	Loss: 1.576540
Train Epoch : 4 [138000/399600 (35%)]	Loss: 1.

Train Epoch : 4 [275000/399600 (69%)]	Loss: 1.579735
Train Epoch : 4 [276000/399600 (69%)]	Loss: 1.580138
Train Epoch : 4 [277000/399600 (69%)]	Loss: 1.570902
Train Epoch : 4 [278000/399600 (70%)]	Loss: 1.580151
Train Epoch : 4 [279000/399600 (70%)]	Loss: 1.582559
Train Epoch : 4 [280000/399600 (70%)]	Loss: 1.566392
Train Epoch : 4 [281000/399600 (70%)]	Loss: 1.573129
Train Epoch : 4 [282000/399600 (71%)]	Loss: 1.569717
Train Epoch : 4 [283000/399600 (71%)]	Loss: 1.560253
Train Epoch : 4 [284000/399600 (71%)]	Loss: 1.599718
Train Epoch : 4 [285000/399600 (71%)]	Loss: 1.569709
Train Epoch : 4 [286000/399600 (72%)]	Loss: 1.553060
Train Epoch : 4 [287000/399600 (72%)]	Loss: 1.563033
Train Epoch : 4 [288000/399600 (72%)]	Loss: 1.596404
Train Epoch : 4 [289000/399600 (72%)]	Loss: 1.583444
Train Epoch : 4 [290000/399600 (73%)]	Loss: 1.585073
Train Epoch : 4 [291000/399600 (73%)]	Loss: 1.590284
Train Epoch : 4 [292000/399600 (73%)]	Loss: 1.599024
Train Epoch : 4 [293000/399600 (73%)]	Loss: 1.

In [37]:
test()

Q 608-240 T 368 ☑ 368
Q 855-302 T 553 ☑ 553
Q 880-392 T 488 ☑ 488
Q 649-297 T 352 ☑ 352
Q 754-091 T 663 ☑ 663
Q 907-105 T 802 ☒ 801
Q 844-454 T 390 ☑ 390
Q 382-312 T 070 ☑ 070
Q 712-177 T 535 ☑ 535
Q 597-264 T 333 ☑ 333
Q 992-800 T 192 ☑ 192
Q 705-658 T 047 ☑ 047
Q 969-080 T 889 ☑ 889
Q 658-358 T 300 ☑ 300
Q 867-262 T 605 ☑ 605
Q 120-042 T 078 ☒ 008
Q 512-263 T 249 ☑ 249
Q 599-421 T 178 ☑ 178
Q 923-675 T 248 ☑ 248
Q 916-384 T 532 ☒ 531
Q 647-089 T 558 ☑ 558
Q 386-230 T 156 ☑ 156
Q 786-450 T 336 ☑ 336
Q 373-172 T 201 ☑ 201
Q 502-308 T 194 ☑ 194
Q 949-922 T 027 ☑ 027
Q 915-732 T 183 ☑ 183
Q 962-945 T 017 ☑ 017
Q 865-460 T 405 ☑ 405
Q 250-111 T 139 ☒ 039
Q 693-501 T 192 ☒ 193
Q 703-160 T 543 ☑ 543
Q 214-012 T 202 ☒ 002
Q 792-132 T 660 ☑ 660
Q 931-105 T 826 ☑ 826
Q 788-591 T 197 ☑ 197
Q 726-416 T 310 ☑ 310
Q 897-027 T 870 ☑ 870
Q 906-362 T 544 ☑ 544
Q 811-242 T 569 ☑ 569
Q 874-668 T 206 ☑ 206
Q 607-368 T 239 ☒ 238
Q 469-020 T 449 ☑ 449
Q 808-733 T 075 ☑ 075
Q 428-111 T 317 ☑ 317
Q 373-096 

Q 939-771 T 168 ☑ 168
Q 979-291 T 688 ☑ 688
Q 547-229 T 318 ☑ 318
Q 800-514 T 286 ☑ 286
Q 202-155 T 047 ☒ 007
Q 919-852 T 067 ☑ 067
Q 983-679 T 304 ☑ 304
Q 336-228 T 108 ☑ 108
Q 745-166 T 579 ☒ 589
Q 555-415 T 140 ☑ 140
Q 578-275 T 303 ☑ 303
Q 972-279 T 693 ☑ 693
Q 504-172 T 332 ☑ 332
Q 339-182 T 157 ☑ 157
Q 937-051 T 886 ☑ 886
Q 701-565 T 136 ☑ 136
Q 505-047 T 458 ☑ 458
Q 898-325 T 573 ☑ 573
Q 259-236 T 023 ☑ 023
Q 901-501 T 400 ☑ 400
Q 968-909 T 059 ☑ 059
Q 369-017 T 352 ☑ 352
Q 365-165 T 200 ☑ 200
Q 668-479 T 189 ☒ 199
Q 900-474 T 426 ☑ 426
Q 545-523 T 022 ☑ 022
Q 724-068 T 656 ☑ 656
Q 276-063 T 213 ☒ 013
Q 976-433 T 543 ☑ 543
Q 570-068 T 502 ☑ 502
Q 629-003 T 626 ☑ 626
Q 347-167 T 180 ☑ 180
Q 856-372 T 484 ☑ 484
Q 974-207 T 767 ☑ 767
Q 541-495 T 046 ☑ 046
Q 974-795 T 179 ☑ 179
Q 863-453 T 410 ☑ 410
Q 721-204 T 517 ☑ 517
Q 872-774 T 098 ☒ 097
Q 714-644 T 070 ☑ 070
Q 456-320 T 136 ☑ 136
Q 622-065 T 557 ☑ 557
Q 514-477 T 037 ☑ 037
Q 655-112 T 543 ☒ 544
Q 992-464 T 528 ☑ 528
Q 879-481 

Q 940-908 T 032 ☑ 032
Q 416-375 T 041 ☒ 040
Q 526-378 T 148 ☑ 148
Q 822-747 T 075 ☑ 075
Q 722-535 T 187 ☑ 187
Q 713-142 T 571 ☑ 571
Q 764-142 T 622 ☑ 622
Q 271-104 T 167 ☒ 067
Q 662-067 T 595 ☑ 595
Q 836-245 T 591 ☑ 591
Q 189-121 T 068 ☒ 158
Q 440-368 T 072 ☑ 072
Q 887-229 T 658 ☑ 658
Q 884-705 T 179 ☑ 179
Q 522-065 T 457 ☑ 457
Q 221-034 T 187 ☒ 007
Q 868-262 T 606 ☑ 606
Q 222-001 T 221 ☒ 021
Q 373-144 T 229 ☑ 229
Q 595-468 T 127 ☑ 127
Q 729-503 T 226 ☑ 226
Q 491-289 T 202 ☑ 202
Q 998-610 T 388 ☑ 388
Q 389-152 T 237 ☑ 237
Q 612-069 T 543 ☑ 543
Q 905-763 T 142 ☒ 141
Q 730-257 T 473 ☑ 473
Q 505-473 T 032 ☒ 031
Q 207-200 T 007 ☑ 007
Q 839-075 T 764 ☑ 764
Q 536-336 T 200 ☑ 200
Q 678-290 T 388 ☑ 388
Q 662-611 T 051 ☑ 051
Q 504-423 T 081 ☑ 081
Q 985-159 T 826 ☑ 826
Q 619-323 T 296 ☑ 296
Q 962-396 T 566 ☑ 566
Q 646-539 T 107 ☑ 107
Q 532-275 T 257 ☑ 257
Q 719-357 T 362 ☑ 362
Q 981-052 T 929 ☑ 929
Q 662-127 T 535 ☑ 535
Q 891-608 T 283 ☑ 283
Q 506-029 T 477 ☑ 477
Q 619-601 T 018 ☑ 018
Q 853-516 

Q 731-519 T 212 ☑ 212
Q 666-047 T 619 ☑ 619
Q 965-069 T 896 ☑ 896
Q 605-317 T 288 ☑ 288
Q 199-031 T 168 ☒ 028
Q 638-369 T 269 ☑ 269
Q 218-177 T 041 ☒ 001
Q 526-276 T 250 ☑ 250
Q 405-392 T 013 ☑ 013
Q 375-108 T 267 ☑ 267
Q 968-012 T 956 ☑ 956
Q 749-248 T 501 ☑ 501
Q 761-360 T 401 ☑ 401
Q 702-111 T 591 ☑ 591
Q 250-068 T 182 ☒ 002
Q 888-467 T 421 ☑ 421
Q 278-040 T 238 ☒ 038
Q 668-251 T 417 ☑ 417
Q 256-021 T 235 ☒ 035
Q 704-600 T 104 ☑ 104
Q 326-080 T 246 ☑ 246
Q 602-278 T 324 ☑ 324
Q 451-401 T 050 ☑ 050
Q 904-663 T 241 ☑ 241
Q 661-000 T 661 ☑ 661
Q 957-620 T 337 ☑ 337
Q 763-104 T 659 ☑ 659
Q 576-184 T 392 ☑ 392
Q 903-502 T 401 ☑ 401
Q 917-577 T 340 ☒ 349
Q 948-532 T 416 ☑ 416
Q 501-299 T 202 ☑ 202
Q 711-558 T 153 ☑ 153
Q 762-325 T 437 ☑ 437
Q 424-137 T 287 ☑ 287
Q 824-061 T 763 ☑ 763
Q 761-326 T 435 ☑ 435
Q 851-356 T 495 ☑ 495
Q 652-200 T 452 ☑ 452
Q 491-027 T 464 ☑ 464
Q 997-304 T 693 ☑ 693
Q 244-230 T 014 ☑ 014
Q 975-278 T 697 ☑ 697
Q 291-135 T 156 ☒ 016
Q 599-543 T 056 ☑ 056
Q 424-039 

Q 885-042 T 843 ☑ 843
Q 855-643 T 212 ☑ 212
Q 628-026 T 602 ☑ 602
Q 959-064 T 895 ☑ 895
Q 648-040 T 608 ☑ 608
Q 632-205 T 427 ☑ 427
Q 991-207 T 784 ☑ 784
Q 557-030 T 527 ☑ 527
Q 510-463 T 047 ☑ 047
Q 301-084 T 217 ☑ 217
Q 504-427 T 077 ☑ 077
Q 985-679 T 306 ☒ 307
Q 533-328 T 205 ☑ 205
Q 609-254 T 355 ☑ 355
Q 863-626 T 237 ☑ 237
Q 304-207 T 097 ☒ 096
Q 955-197 T 758 ☑ 758
Q 927-800 T 127 ☑ 127
Q 985-983 T 002 ☑ 002
Q 570-539 T 031 ☑ 031
Q 580-484 T 096 ☑ 096
Q 321-180 T 141 ☑ 141
Q 913-893 T 020 ☒ 030
Q 974-418 T 556 ☑ 556
Q 749-356 T 393 ☑ 393
Q 321-008 T 313 ☑ 313
Q 989-339 T 650 ☑ 650
Q 385-286 T 099 ☑ 099
Q 458-310 T 148 ☑ 148
Q 422-098 T 324 ☑ 324
Q 246-185 T 061 ☒ 001
Q 966-537 T 429 ☑ 429
Q 684-551 T 133 ☑ 133
Q 947-129 T 818 ☑ 818
Q 334-005 T 329 ☑ 329
Q 268-087 T 181 ☒ 001
Q 927-536 T 391 ☒ 390
Q 943-041 T 902 ☑ 902
Q 865-792 T 073 ☑ 073
Q 534-266 T 268 ☑ 268
Q 802-005 T 797 ☑ 797
Q 922-371 T 551 ☑ 551
Q 528-054 T 474 ☑ 474
Q 652-261 T 391 ☑ 391
Q 424-201 T 223 ☑ 223
Q 493-240 

...

Q 948-468 T 480 ☑ 480
Q 689-246 T 443 ☑ 443
Q 801-161 T 640 ☑ 640
Q 343-313 T 030 ☑ 030
Q 796-406 T 390 ☑ 390
Q 445-333 T 112 ☑ 112
Q 916-321 T 595 ☑ 595
Q 974-884 T 090 ☑ 090
Q 579-188 T 391 ☑ 391
Q 585-281 T 304 ☑ 304
Q 960-834 T 126 ☑ 126
Q 970-074 T 896 ☑ 896
Q 884-473 T 411 ☑ 411
Q 103-019 T 084 ☒ 004
Q 317-229 T 088 ☑ 088
Q 465-377 T 088 ☑ 088
Q 785-199 T 586 ☑ 586
Q 793-436 T 357 ☑ 357
Q 806-683 T 123 ☒ 121
Q 777-173 T 604 ☑ 604
Q 786-288 T 498 ☑ 498
Q 246-038 T 208 ☒ 008
Q 145-073 T 072 ☒ 002
Q 578-418 T 160 ☑ 160
Q 434-252 T 182 ☑ 182
Q 469-043 T 426 ☑ 426
Q 573-393 T 180 ☑ 180
Q 719-681 T 038 ☑ 038
Q 519-172 T 347 ☑ 347
Q 724-446 T 278 ☑ 278
Q 434-288 T 146 ☑ 146
Q 874-560 T 314 ☑ 314
Q 650-443 T 207 ☑ 207
Q 243-093 T 150 ☒ 000
Q 773-390 T 383 ☑ 383
Q 670-497 T 173 ☑ 173
Q 994-008 T 986 ☑ 986
Q 570-122 T 448 ☑ 448
Q 760-696 T 064 ☑ 064
Q 893-234 T 659 ☑ 659
Q 826-345 T 481 ☑ 481
Q 395-386 T 009 ☑ 009
Q 702-474 T 228 ☒ 227
Q 756-745 T 011 ☑ 011
Q 467-363 T 104 ☑ 104
Q 291-191 

Q 793-045 T 748 ☑ 748
Q 338-195 T 143 ☑ 143
Q 497-136 T 361 ☑ 361
Q 535-079 T 456 ☒ 457
Q 624-382 T 242 ☒ 241
Q 266-076 T 190 ☒ 000
Q 486-260 T 226 ☑ 226
Q 498-245 T 253 ☑ 253
Q 902-022 T 880 ☑ 880
Q 834-229 T 605 ☑ 605
Q 377-337 T 040 ☑ 040
Q 825-697 T 128 ☑ 128
Q 874-563 T 311 ☑ 311
Q 679-646 T 033 ☑ 033
Q 208-057 T 151 ☒ 001
Q 772-136 T 636 ☑ 636
Q 430-061 T 369 ☑ 369
Q 700-051 T 649 ☑ 649
Q 784-319 T 465 ☑ 465
Q 455-075 T 380 ☑ 380
Q 523-223 T 300 ☑ 300
Q 589-089 T 500 ☑ 500
Q 571-407 T 164 ☑ 164
Q 473-218 T 255 ☑ 255
Q 883-827 T 056 ☑ 056
Q 570-524 T 046 ☑ 046
Q 761-460 T 301 ☑ 301
Q 501-258 T 243 ☑ 243
Q 754-195 T 559 ☑ 559
Q 553-075 T 478 ☑ 478
Q 851-089 T 762 ☑ 762
Q 684-084 T 600 ☑ 600
Q 557-243 T 314 ☑ 314
Q 424-129 T 295 ☑ 295
Q 108-064 T 044 ☒ 004
Q 202-187 T 015 ☒ 005
Q 798-678 T 120 ☑ 120
Q 497-447 T 050 ☑ 050
Q 326-151 T 175 ☑ 175
Q 542-511 T 031 ☑ 031
Q 660-224 T 436 ☑ 436
Q 651-579 T 072 ☑ 072
Q 582-555 T 027 ☑ 027
Q 796-293 T 503 ☑ 503
Q 428-352 T 076 ☑ 076
Q 983-408 

Q 802-645 T 157 ☑ 157
Q 599-566 T 033 ☑ 033
Q 707-518 T 189 ☑ 189
Q 860-130 T 730 ☑ 730
Q 664-120 T 544 ☑ 544
Q 525-374 T 151 ☑ 151
Q 534-120 T 414 ☑ 414
Q 132-129 T 003 ☑ 003
Q 983-368 T 615 ☑ 615
Q 756-692 T 064 ☑ 064
Q 654-174 T 480 ☑ 480
Q 373-171 T 202 ☑ 202
Q 890-690 T 200 ☑ 200
Q 871-242 T 629 ☑ 629
Q 750-704 T 046 ☒ 045
Q 905-900 T 005 ☑ 005
Q 994-490 T 504 ☑ 504
Q 324-101 T 223 ☑ 223
Q 845-775 T 070 ☑ 070
Q 372-292 T 080 ☑ 080
Q 621-048 T 573 ☑ 573
Q 902-032 T 870 ☑ 870
Q 818-536 T 282 ☑ 282
Q 715-356 T 359 ☑ 359
Q 891-752 T 139 ☒ 039
Q 629-349 T 280 ☑ 280
Q 136-133 T 003 ☑ 003
Q 646-237 T 409 ☑ 409
Q 959-838 T 121 ☑ 121
Q 081-036 T 045 ☒ 025
Q 236-099 T 137 ☒ 007
Q 904-562 T 342 ☒ 341
Q 713-228 T 485 ☑ 485
Q 968-781 T 187 ☑ 187
Q 428-215 T 213 ☑ 213
Q 649-094 T 555 ☑ 555
Q 453-324 T 129 ☑ 129
Q 766-150 T 616 ☑ 616
Q 798-253 T 545 ☑ 545
Q 874-458 T 416 ☑ 416
Q 703-048 T 655 ☑ 655
Q 594-336 T 258 ☑ 258
Q 909-551 T 358 ☑ 358
Q 760-162 T 598 ☑ 598
Q 778-441 T 337 ☑ 337
Q 777-387 

Q 600-407 T 193 ☑ 193
Q 394-036 T 358 ☑ 358
Q 721-357 T 364 ☑ 364
Q 735-184 T 551 ☑ 551
Q 512-452 T 060 ☑ 060
Q 224-176 T 048 ☒ 008
Q 972-411 T 561 ☑ 561
Q 932-834 T 098 ☒ 097
Q 176-021 T 155 ☒ 055
Q 835-097 T 738 ☑ 738
Q 653-317 T 336 ☑ 336
Q 966-925 T 041 ☑ 041
Q 855-428 T 427 ☑ 427
Q 784-125 T 659 ☑ 659
Q 859-623 T 236 ☑ 236
Q 480-146 T 334 ☑ 334
Q 348-088 T 260 ☑ 260
Q 461-201 T 260 ☑ 260
Q 934-150 T 784 ☑ 784
Q 986-891 T 095 ☑ 095
Q 537-418 T 119 ☑ 119
Q 785-437 T 348 ☑ 348
Q 641-192 T 449 ☑ 449
Q 719-464 T 255 ☑ 255
Q 851-152 T 699 ☑ 699
Q 669-106 T 563 ☑ 563
Q 429-398 T 031 ☑ 031
Q 733-732 T 001 ☑ 001
Q 201-040 T 161 ☒ 001
Q 925-072 T 853 ☑ 853
Q 996-732 T 264 ☑ 264
Q 661-607 T 054 ☑ 054
Q 264-238 T 026 ☑ 026
Q 720-423 T 297 ☑ 297
Q 651-347 T 304 ☑ 304
Q 329-327 T 002 ☑ 002
Q 745-518 T 227 ☑ 227
Q 875-747 T 128 ☑ 128
Q 883-351 T 532 ☑ 532
Q 856-571 T 285 ☑ 285
Q 958-033 T 925 ☑ 925
Q 229-208 T 021 ☑ 021
Q 946-906 T 040 ☑ 040
Q 583-138 T 445 ☑ 445
Q 772-084 T 688 ☑ 688
Q 951-438 

Q 607-503 T 104 ☑ 104
Q 769-558 T 211 ☑ 211
Q 975-603 T 372 ☑ 372
Q 842-225 T 617 ☑ 617
Q 653-071 T 582 ☑ 582
Q 571-372 T 199 ☑ 199
Q 669-500 T 169 ☑ 169
Q 939-893 T 046 ☑ 046
Q 335-208 T 127 ☑ 127
Q 243-086 T 157 ☒ 007
Q 884-074 T 810 ☑ 810
Q 608-575 T 033 ☑ 033
Q 161-051 T 110 ☒ 010
Q 867-553 T 314 ☑ 314
Q 993-863 T 130 ☑ 130
Q 893-589 T 304 ☑ 304
Q 558-362 T 196 ☑ 196
Q 786-335 T 451 ☑ 451
Q 963-620 T 343 ☑ 343
Q 310-103 T 207 ☑ 207
Q 668-421 T 247 ☑ 247
Q 823-445 T 378 ☑ 378
Q 408-368 T 040 ☑ 040
Q 557-302 T 255 ☑ 255
Q 970-275 T 695 ☑ 695
Q 775-341 T 434 ☑ 434
Q 860-495 T 365 ☑ 365
Q 192-083 T 109 ☒ 009
Q 890-018 T 872 ☑ 872
Q 303-298 T 005 ☑ 005
Q 880-503 T 377 ☑ 377
Q 977-823 T 154 ☑ 154
Q 781-156 T 625 ☑ 625
Q 981-680 T 301 ☑ 301
Q 397-288 T 109 ☑ 109
Q 442-080 T 362 ☑ 362
Q 951-021 T 930 ☑ 930
Q 620-243 T 377 ☑ 377
Q 869-625 T 244 ☑ 244
Q 853-751 T 102 ☑ 102
Q 632-401 T 231 ☑ 231
Q 814-034 T 780 ☑ 780
Q 658-126 T 532 ☑ 532
Q 799-360 T 439 ☑ 439
Q 868-358 T 510 ☑ 510
Q 248-002 

# 作業報告小心得

一開始在猶豫要選用 keras 還是 pytorch<br>
後來被網路上評論說服說一個新的且沒那麼抽象的框架

隨即遇到的第一個困難就是<br>
我該怎麼在 pytorch 重現範例<br>
為此看了 pytorch document 嘗試了解後自己重現

但搞到最後，我稍微懂了 pytorch 卻搞不懂 keras<br>
所以選擇大概參考 model 的建立後

就開始想自己的 RNN 減法器該怎麼寫

老實說，好多都不懂<br>
但寫下去也發現學到好多

可惜就是我自己太晚開始寫這作業

整體來說:收穫良多~~~